In [3]:
!pip install rasterio

Defaulting to user installation because normal site-packages is not writeable


In [12]:
import os
import numpy as np
import rasterio
from rasterio.warp import calculate_default_transform, reproject, Resampling
from rasterio.transform import from_origin
from tqdm import tqdm

def reproject_raster(src_path, dst_path, target_crs="EPSG:3035"):
    """Reprojects a raster to a target CRS and saves it."""
    with rasterio.open(src_path) as src:
        transform, width, height = calculate_default_transform(
            src.crs, target_crs, src.width, src.height, *src.bounds
        )
        kwargs = src.meta.copy()
        kwargs.update({
            'crs': target_crs,
            'transform': transform,
            'width': width,
            'height': height
        })

        with rasterio.open(dst_path, 'w', **kwargs) as dst:
            for i in range(1, src.count + 1):
                reproject(
                    source=rasterio.band(src, i),
                    destination=rasterio.band(dst, i),
                    src_transform=src.transform,
                    src_crs=src.crs,
                    dst_transform=transform,
                    dst_crs=target_crs,
                    resampling=Resampling.nearest
                )

def split_geotiff(
    rasters_path,
    output_dir,
    width=15,
    height=15,
    pixel_size=1.6,
    target_crs="EPSG:3035",
    skip_black_threshold=0.1,
    verbose=True
):
    """Splits GeoTIFF raster images into tiles."""
    
    os.makedirs(output_dir, exist_ok=True)

    tif_files = [f for f in os.listdir(rasters_path) if f.lower().endswith(".tif")]
    if verbose and not tif_files:
        print("⚠️ No .tif files found in:", rasters_path)

    raster_id = 0

    for tif_file in tqdm(tif_files, desc="Processing rasters"):
        raster_id += 1
        img_id = os.path.splitext(tif_file)[0]
        raster_path = os.path.join(rasters_path, tif_file)

        # Temporary path for reprojected raster
        temp_path = os.path.join(output_dir, f"temp_reprojected_{img_id}.tif")
        reproject_raster(raster_path, temp_path, target_crs=target_crs)

        with rasterio.open(temp_path) as src:
            image = src.read()
            meta = src.meta
            transform = src.transform

            heights = np.arange(0, image.shape[1], height)
            widths = np.arange(0, image.shape[2], width)
            min_x = transform[2]
            max_y = transform[5]

            for x in range(len(heights) - 1):
                for y in range(len(widths) - 1):
                    tile = image[:, heights[x]:heights[x+1], widths[y]:widths[y+1]]

                    black_mask = np.all(tile == 0, axis=0)
                    black_fraction = np.sum(black_mask) / black_mask.size

                    if black_fraction > skip_black_threshold:
                        if verbose:
                            print(f"Skipping black tile at {heights[x]}, {widths[y]} ({black_fraction:.2%} black)")
                        continue

                    tile_transform = from_origin(
                        min_x + widths[y] * pixel_size,
                        max_y - heights[x] * pixel_size,
                        pixel_size,
                        pixel_size
                    )

                    meta.update({
                        "driver": "GTiff",
                        "height": tile.shape[1],
                        "width": tile.shape[2],
                        "transform": tile_transform
                    })

                    tile_filename = os.path.join(
                        output_dir,
                        f"{raster_id}_{img_id}_{heights[x]}_{widths[y]}.tif"
                    )

                    with rasterio.open(tile_filename, "w", compress='lzw', **meta) as dest:
                        dest.write(tile)

        # Optionally delete the temporary reprojected raster
        os.remove(temp_path)

    if verbose:
        print("✅ Finished tiling all rasters.")


In [13]:
import os

folder_path = r"C:\SatelliteImagery"
files = os.listdir(folder_path)
tif_files = [file for file in files if file.lower().endswith('.tif')]

print("Found .tif files:", tif_files)


Found .tif files: ['Test1.tif']


In [ ]:
split_geotiff(
    rasters_path=r"C:\SatelliteImagery",
    output_dir=r"C:\SatelliteImagery\Test"
)

Processing rasters:   0%|                                                                        | 0/1 [00:00<?, ?it/s]

Skipping black tile at 0, 0 (100.00% black)
Skipping black tile at 0, 15 (100.00% black)
Skipping black tile at 0, 30 (100.00% black)
Skipping black tile at 0, 45 (100.00% black)
Skipping black tile at 0, 60 (100.00% black)
Skipping black tile at 0, 75 (100.00% black)
Skipping black tile at 0, 90 (100.00% black)
Skipping black tile at 0, 105 (100.00% black)
Skipping black tile at 0, 120 (100.00% black)
Skipping black tile at 0, 135 (100.00% black)
Skipping black tile at 0, 150 (100.00% black)
Skipping black tile at 0, 165 (100.00% black)
Skipping black tile at 0, 180 (100.00% black)
Skipping black tile at 0, 195 (100.00% black)
Skipping black tile at 0, 210 (100.00% black)
Skipping black tile at 0, 225 (100.00% black)
Skipping black tile at 0, 240 (100.00% black)
Skipping black tile at 0, 255 (100.00% black)
Skipping black tile at 0, 270 (100.00% black)
Skipping black tile at 0, 285 (100.00% black)
Skipping black tile at 0, 300 (100.00% black)
Skipping black tile at 0, 315 (100.00% bla